In [ ]:
import time
import json
import datetime

import cvxpy as cp
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

In [ ]:
# Total duration (minutes).
T = 60 * 24 * 5
# Sampling interval (minutes).
dt = 30
time_steps = T // dt

TIMES = np.arange(0, T, dt)

CAPACITY = 2000
CAPACITY_INITIAL = CAPACITY / 4

In [ ]:
DEMAND_MIN = -16
DEMAND_MAX = 7
PERIOD = 1440

DEMAND = DEMAND_MIN + (DEMAND_MAX - DEMAND_MIN) / 2 * (
    1 + np.sin(2 * np.pi * TIMES / PERIOD)
)
DEMAND = np.maximum(DEMAND, 0)

In [ ]:
n_steps = len(TIMES)

iflow = cp.Variable(n_steps, nonneg=True)
oflow = cp.Variable(n_steps, nonneg=True)
level = cp.Variable(n_steps, nonneg=True)

Initial guess.

In [ ]:
oflow.value = np.full(n_steps, 0)

## Constraints

In [ ]:
constraints = []

In [ ]:
# Initial level.
constraints.append(level[0] == CAPACITY_INITIAL)

# Level dynamics.
for t in range(1, n_steps):
    constraints.append(
        level[t] == level[t - 1] + (iflow[t - 1] - oflow[t - 1]) * dt
    )
# Level constraint for last step since final outflow not constrained by level dynamics.
constraints.append(oflow[-1] <= level[-1] / dt)

# Capacity.
constraints += [level <= CAPACITY]

In [ ]:
# Pump flow constraints
constraints += [
    iflow >= 0,
    iflow <= 5,
    oflow >= 0,
    oflow <= 50,
]

## Objective

In [ ]:
# Smoothing terms (suppress change between successive values).
ismooth = cp.norm1(iflow[1:] - iflow[:-1])
osmooth = cp.norm1(oflow[1:] - oflow[:-1])

difference = cp.norm1(oflow - DEMAND)

objective = cp.Minimize(difference + 0.1 * ismooth + 0.1 * osmooth)

## Optimise

In [ ]:
# Get list of installed solvers.
cp.installed_solvers()

In [ ]:
SOLVER = cp.OSQP
kwargs = {"max_iter": 100000,}

# SOLVER = cp.MOSEK
# kwargs = {}

# SOLVER = cp.SCS
# kwargs = {}

In [ ]:
problem = cp.Problem(objective, constraints)

start = time.perf_counter()
#
problem.solve(
    solver=SOLVER,    
    verbose=True,
    **kwargs,
)
#
end = time.perf_counter()

In [ ]:
print(f"Time: {end - start:.6f} seconds")

In [ ]:
results = pd.DataFrame({
    "time": TIMES,
    "demand": DEMAND,
    "inflow": iflow.value,
    "outflow": oflow.value,
    "level": level.value,
})

In [ ]:
fig, axes = plt.subplots(3, 1, figsize=(8, 8))

sns.lineplot(
    data=results,
    x="time",
    y="inflow",
    drawstyle="steps-pre",
    color="#27ae60",
    ax=axes[0],
)
axes[0].set_title("Inflow Rate")
axes[0].set(ylabel=None)
axes[0].set_ylim(1.25, 3.5)
axes[0].grid(axis="y", color="lightgrey", linestyle="--", linewidth=0.5)

sns.lineplot(
    data=results,
    x="time",
    y="demand",
    color="black",
    ax=axes[1],
)
sns.lineplot(
    data=results,
    x="time",
    y="outflow",
    drawstyle="steps-pre",
    color="#3498db",
    ax=axes[1],
)
axes[1].set_title("Outflow Rate")
axes[1].set(ylabel=None)

sns.lineplot(
    data=results,
    x="time",
    y="level",
    color="black",
    ax=axes[2],
)
axes[2].set_title("Tank Level")
axes[2].set(ylabel=None)

plt.tight_layout()

plt.savefig(f"tank-global-cvxpy-solution-{str(SOLVER).lower()}.png", format="png", dpi=300)

plt.show()

In [ ]:
with open(f"tank-global-cvxpy-solution-{str(SOLVER).lower()}.json", "w") as f:
    json.dump(
        {
            "objective": round(problem.value, 3),
            "time": round(end - start, 3),
            "timestamp": datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S"),
        },
        f, indent=4
    )

In [ ]:
data = [(constraint.__class__.__name__, constraint.value()) for constraint in constraints]

summary = {}

for category, value in data:
    if category not in summary:
        summary[category] = {'True': 0, 'False': 0}
    if value:
        summary[category]['True'] += 1
    else:
        summary[category]['False'] += 1

for category, counts in summary.items():
    total = counts['True'] + counts['False']
    summary[category]['True'] = counts['True'] / total
    summary[category]['False'] = counts['False'] / total

# It looks like the equality constraints are not satisfied. Perhaps this is due to numerical precision?
summary